# MAP PLOT USING FOLIUM (CHARITY PROJECT)
AS A VOLUNTEER AT THE ROBERT'S CHARITY FOUNDATION,THIS WAS TO PLOT A GEOGRAPHIC MAP TO SHOW AREAS IN NIGERIA (PORTHARCOURT AND LAGOS) THAT NEEDED OUR VOLUNTEER HOURS, ITEMS NEEDED, ITEMS GIVEN, PROJECTS DONE, PROJECTS ONGOING, ETC.

# TO VIEW MAP ON WEB --> https://github.com/leosj1/rcf/blob/master/rcm.html <--- RIGHT CLICK ON 'Download' TAB AND CLICK 'Save link as...'

In [5]:
import json
path='C:\\Users\\Leo-SJ\\Documents\\MASTERS\\'
with open("C:\\Users\\Leo-SJ\\Documents\\MASTERS\\convert (2).json") as f: #loading the converted shapefile in json showing states, their local governments and coordinates
    nigeria_data=json.load(f)
lat=[0]
long=[0]

#Get the average of the longitude and latiutude of each states and their local governments and append to an array "latlong".
latlong=[]

for state in range(len(nigeria_data['features'])):
    total_x=0
    total_y=0
    data=nigeria_data['features'][state]['geometry']['coordinates'][0]
    l=len(data)
    for i in range(l-1):
        total_x+=data[i][0]
        total_y+=data[i][1]
    latlong.append([nigeria_data['features'][state]['properties']['ADM1'],nigeria_data['features'][state]['properties']['ADM2'],total_x/l,total_y/l])
# latlong

In [2]:
nigeria_data['features'][0] #view of nigeria_data structure

{'type': 'Feature',
 'properties': {'ID': 1,
  'LBL': 'NIR-1',
  'FIP': 'NI',
  'MMT_ID': 'NIR',
  'SHORT__FRM': 'Nigeria',
  'LONG_FRM': 'Federal Republic of Nigeria',
  'ADM0': 'Nigeria',
  'ADM1': 'Abia',
  'ADM2': 'Aba',
  'ADM3': '-',
  'ADM4': '-',
  'ADM5': '-',
  'STL-0': 168,
  'STL-1': 1,
  'STL-2': 11,
  'STL-3': '-',
  'STL-4': '-',
  'STL-5': '-'},
 'geometry': {'type': 'Polygon',
  'coordinates': [[[7.289999961853027, 5.059999942779541],
    [7.28000020980835, 5.079999923706055],
    [7.28000020980835, 5.090000152587891],
    [7.28000020980835, 5.099999904632568],
    [7.289999961853027, 5.110000133514404],
    [7.300000190734863, 5.110000133514404],
    [7.300000190734863, 5.130000114440918],
    [7.320000171661377, 5.139999866485596],
    [7.329999923706055, 5.150000095367432],
    [7.340000152587891, 5.150000095367432],
    [7.349999904632568, 5.139999866485596],
    [7.360000133514404, 5.139999866485596],
    [7.360000133514404, 5.130000114440918],
    [7.369999885559

In [3]:
#CONVERT ARRAY "latlong" TO A DATAFRAME "df"
import pandas as pd
df=pd.DataFrame(latlong)
df.rename(columns={0:'states',1:'local_govt',2:'long',3:'lat'},inplace=True) #change column names to appropriate ones
df.groupby('states').first().head() #view few data in dataframe

# df.loc[(df['states']=='Rivers') & (df['states'].=='Lagos')]
# df.loc[df['states'].isin(['Rivers','Lagos'])].groupby('states').first()

local_govt       long       lat
states                                   
Abia             Aba   7.034400  4.894800
Adamawa       Fufore  12.621060  9.116739
Akwa Ibom       Abak   7.590566  4.920000
Anambra       Aguata   6.813333  5.785333
Bauchi      Alkaleri  10.415723  9.858855

In [6]:
#LOADING COMPILED LIST OF SCHOOLS, AREAS, AND ITEMS NEEDED/GIVEN FROM EXCEL TO A DATAFRAME "latlong2" FOR PORTHARCOURT AND LAGOS
latlong2=pd.read_excel(path+'ph_lag.xlsx',na_values=True) #loading data from excel to a panda dataframe
latlong2.groupby('state').first() #viewing few data in the dataframe representing Portharcourt and Lagos

local_govt       lon       lat  TEXTBOOKS  NOTEBOOKS  BAGS  \
state                                                               
Lagos       Agege  3.197600  6.386000  TEXTBOOKS  NOTEBOOKS  BAGS   
Rivers   Abua/Odu  6.419636  4.735818  TEXTBOOKS  NOTEBOOKS  BAGS   

        SCHOLARSHIPS  SANDALS  STATIONERY         LOW_VISION_GLASSES  \
state                                                                  
Lagos   SCHOLARSHIPS  SANDALS  STATIONERY                        NaN   
Rivers  SCHOLARSHIPS  SANDALS  STATIONERY  LOWVISIONGLASSES-N300,000   

                                                   SCHOOL    AMOUNT  
state                                                                
Lagos                                                 NaN   N50,000  
Rivers  OLANADA  SCHOOL 1, OLANADA  SCHOOL 2, COMMUNIT...  N200,000

In [7]:
#SEPARATING AREAS WHERE PROJECTS HAVE BEEN DONE, ONGOING AND NOT STARTED
not_started=[]
started=[]
#IF DATA TYPE IN DATAFRAME FOR "NaN" WHICH WAS "float", THEN APPEND TO "not_started" array
for lat,lon,state,lg,tb,nb,bg,sch,snd,stat,lvg in zip(latlong2['lat'],latlong2['lon'],latlong2['state'],latlong2['local_govt'],latlong2['TEXTBOOKS'],latlong2['NOTEBOOKS'],latlong2['BAGS'],latlong2['SCHOLARSHIPS'],latlong2['SANDALS'],latlong2['STATIONERY'],latlong2['LOW_VISION_GLASSES']): 
    if type(tb)==float:
        if type(nb)==float:
            if type(bg)==float:
                if type(sch)==float:
                    if type(snd)==float:
                        if type(stat)==float:
                            if type(lvg)==float:
                                not_started.append(lg)
        
not_started
#IF DATA IN 'latlong2' DOES NOT EXISTS IN "not_started" array, then append in 'started' array
for data in latlong2['local_govt']:
    if data not in not_started:
        started.append(data)
# started=latlong[1]-not_started
started[0:5]

['Agege', 'Epe', 'Eti-Osa', 'Ikorodu', 'Akukutor']

In [8]:
#ADDING A "status" ELEMENT IN THE "nigeria_data" json DATA
for i in range(len(nigeria_data['features'])):
    #IF DATA EXISTS IN "not_started" array, append "status" as 'in_progress'
    if nigeria_data['features'][i]['properties']['ADM2'] in not_started:
        nigeria_data['features'][i]['properties']['status']='in_progress'
    #IF DATA EXISTS IN "started" array, append "status" as 'done'
    elif nigeria_data['features'][i]['properties']['ADM2'] in started:
        nigeria_data['features'][i]['properties']['status']='done'
    #ELSE DATA DOES NOT EXIST SO APPEND "status" as 'not_started'
    else:
        nigeria_data['features'][i]['properties']['status']='not_started'

In [22]:
#USING FOLIUM LIBRARY TO PLOT THE MAP

import folium
from folium import plugins

map=folium.Map(location=[df['lat'].mean(),df['long'].mean()],zoom_start=6.3,tiles='OpenStreetMap') #GIVE COORDINATES OF THE AREA WHICH IS NIGERIA

# items=['TEXTBOOKS','NOTEBOOKS','BAGS','SCHOLARSHIPS','STATIONERY','LVG','SANDAL'] 

m = folium.plugins.MarkerCluster(control=False)
# mcg=folium.FeatureGroup(name='ITEMS GIVEN / NEEDED')
map.add_child(m)

# for i in items:
#     i=folium.plugins.FeatureGroupSubGroup(mcg,str(i))
#     map.add_child(i)

#SPECIFYING DIFFERENT LAYERS IN THE MAP   
TEXTBOOKS=folium.plugins.FeatureGroupSubGroup(m,'TEXTBOOKS')
map.add_child(TEXTBOOKS)

NOTEBOOKS=folium.plugins.FeatureGroupSubGroup(m,'NOTEBOOKS')
map.add_child(NOTEBOOKS)

BAGS=folium.plugins.FeatureGroupSubGroup(m,'BAGS')
map.add_child(BAGS)

SCHOLARSHIPS=folium.plugins.FeatureGroupSubGroup(m,'SCHOLARSHIPS')
map.add_child(SCHOLARSHIPS)

STATIONERY=folium.plugins.FeatureGroupSubGroup(m,'STATIONERY')
map.add_child(STATIONERY)

LVG=folium.plugins.FeatureGroupSubGroup(m,'LOW VISION GLASSES')
map.add_child(LVG)

SANDAL=folium.plugins.FeatureGroupSubGroup(m,'SANDAL')
map.add_child(SANDAL)

#GROUPING THE DIRRERENT ITEMS WITH DIFFERENT COLORS AND ADD MARKERS TO THE MAP
for lat,lon,state,lg,tb,nb,bg,sch,snd,stat,lvg,amt in zip(latlong2['lat'],latlong2['lon'],latlong2['state'],latlong2['local_govt'],latlong2['TEXTBOOKS'],latlong2['NOTEBOOKS'],latlong2['BAGS'],latlong2['SCHOLARSHIPS'],latlong2['SANDALS'],latlong2['STATIONERY'],latlong2['LOW_VISION_GLASSES'],latlong2['AMOUNT']):
    folium.Circle([lat,lon],radius=40).add_to(map)
    if tb=='TEXTBOOKS':
        folium.Marker(location=[lat,lon],popup=(folium.Popup("@"+lg+" "+str(amt))),icon=folium.Icon(color='Blue',icon_color='Blue')).add_to(map).add_to(TEXTBOOKS)
    if bg=='BAGS':
        folium.Marker(location=[lat,lon],popup=(folium.Popup("@"+lg+" "+str(amt))),icon=folium.Icon(color='Green',icon_color='Green')).add_to(map).add_to(BAGS)
    if nb=='NOTEBOOKS':
        folium.Marker(location=[lat,lon],popup=(folium.Popup("@"+lg+" "+str(amt))),icon=folium.Icon(color='Black',icon_color='Black')).add_to(map).add_to(NOTEBOOKS)
    if stat=='STATIONERY':
        folium.Marker(location=[lat,lon],popup=(folium.Popup("@"+lg+" "+str(amt))),icon=folium.Icon(color='Orange',icon_color='Orange')).add_to(map).add_to(STATIONERY)
    if sch=='SCHOLARSHIPS':
        folium.Marker(location=[lat,lon],popup=(folium.Popup("@"+lg+" "+str(amt))),icon=folium.Icon(color='Purple',icon_color='Purple')).add_to(map).add_to(SCHOLARSHIPS)
    if str(lvg).find('LOWVISIONGLASSES')==0:
        folium.Marker(location=[lat,lon],popup=(folium.Popup("@"+lg+" "+lvg)),icon=folium.Icon(color='Yellow',icon_color='Yellow')).add_to(map).add_to(LVG)
    if lvg=='SANDAL':
        folium.Marker(location=[lat,lon],popup=(folium.Popup("@"+lg+" "+str(amt))),icon=folium.Icon(color='White',icon_color='White')).add_to(map).add_to(SANDAL)
#     fg.add_child(folium.Marker(location=[lat,lon],popup=(folium.Popup(lg)),icon=folium.Icon(color=color(state),icon_color='red')))


# style="position: fixed;
# bottom: 50px;
# left: 50px;
# width: 150px;
# height: 280px;
# border: 2px solid grey;
# z-index: 9999;

#ADDING A LEGEND TO THE MAP IN HTML TAGS
lgnd_html='''
<div style="position:relative;
width:50%
border: 5px solid grey;
">
<div 
style="position: absolute;
bottom: 50px;
left: 50px;
width: 100%;
height: 100%;
border: 5px solid grey;
z-index: 9999;"> 

&nbsp; <strong style="text-color:white;">ITEMS LEGEND</strong> <br> <br><br> &nbsp;

<strong>TEXTBOOKS</strong> &nbsp;
<i class = "fa-rotate-0 glyphicon glyphicon-info-sign fa-1x"
style="color:blue"></i>
<br>&nbsp;

<strong>BAGS</strong> &nbsp; 
<i class = "fa-rotate-0 glyphicon glyphicon-info-sign"
style="color:green"></i>
<br>&nbsp;

<strong>NOTEBOOKS</strong> &nbsp;
<i class = "fa-rotate-0 glyphicon glyphicon-info-sign"
style="color:black"></i>
<br>&nbsp;

<strong>STATIONERY</strong> &nbsp; 
<i class = "fa-rotate-0 glyphicon glyphicon-info-sign"
style="color:orange"></i>
<br>&nbsp;

<strong>SCHOLARSHIPS</strong> &nbsp;
<i class = "fa-rotate-0 glyphicon glyphicon-info-sign"
style="color:purple"></i>
<br>&nbsp; 

<strong>LOW VISION GLASSES</strong> &nbsp; 
<i class = "fa-rotate-0 glyphicon glyphicon-info-sign"
style="color:yellow"></i>
<br>&nbsp;

<strong>SANDALS</strong> &nbsp; 
<i class = "fa-rotate-0 glyphicon glyphicon-info-sign"
style="color:white"></i>
</div></div>'''

#ADD HTML LEGEND TO MAP LAYER
map.get_root().html.add_child(folium.Element(lgnd_html))

# fg2=folium.FeatureGroup(name="Bags")

# <div class="awesome-marker-icon-Green awesome-marker leaflet-zoom-animated leaflet-interactive" tabindex="0" style="margin-left: -17px; margin-top: -42px; width: 35px; height: 45px; opacity: 1; transform: translate3d(598px, 640px, 0px); z-index: 1000640;"><i style="color: Green" class="fa-rotate-0 glyphicon glyphicon-info-sign  "></i></div>
# <i class="fa fa-map-marker fa-2x" style="color:green"></i>
# map.add_child(fg)
# map.add_child(fg2)


#GROUPING COLORS FOR THE DIFFERENT AREAS SHOWING DONE, ONGOING AND NOT STARTED PROJECTS
map.add_child(folium.GeoJson(data=nigeria_data,
                             name="DONE",overlay=False,
                             style_function=lambda x:{'fillColor':
                                 'green' if x['properties']['status']=='done' else
                                 'white'                   
                             }).add_to(map))
map.add_child(folium.GeoJson(data=nigeria_data,
                             name="ON GOING",overlay=False,
                             style_function=lambda x:{'fillColor':
                                 'yellow' if x['properties']['status']=='in_progress' else
                                'white'                    
                             }))
map.add_child(folium.GeoJson(data=nigeria_data,
                             name="NOT STARTED",overlay=False,
                             style_function=lambda x:{'fillColor':
                                 'red' if x['properties']['status']=='not_started' else
                                  'white'
                             }))
folium.LayerControl(collapsed=False).add_to(map)
# map.add_child(folium.LayerControl(collapsed=False))
map.save(outfile='rcm.html')   #SAVE MAP IN HTML EXTENSION
map

# TO VIEW MAP ON WEB--> https://github.com/leosj1/rcf/blob/master/rcm.html <--- RIGHT CLICK ON 'Download' TAB AND CLICK 'Save As'